<a href="https://colab.research.google.com/github/susanje/susanje/blob/main/Untitled4.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

**Cargo las librerias a utilizar**

In [1]:
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import matplotlib.pyplot as plt
import pandas as pd
from itertools import cycle, islice
import datetime as dt
from datetime import datetime, date
import numpy as np
from math import sqrt
from sklearn import linear_model 
from sklearn.preprocessing import PolynomialFeatures

In [2]:
from google.colab import files   
uploaded = files.upload()

Saving Real Estate Data Assessment.xlsx to Real Estate Data Assessment (6).xlsx


**Importo el archivo analizar**

In [32]:
import io 
  
data = pd.read_excel(io.BytesIO(uploaded['Real Estate Data Assessment.xlsx'])) 
print(data)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



**Veo la dimensionalidad del dataset**

In [33]:
data.shape

(22655, 10)

**Comienzo a analizar la información que contiene**

In [34]:
data.head(10)

inmueble    oferta      region          barrio    ciudad  area_metros  \
0  Apartamento  Arriendo  NorOriente    La Milagrosa  Medellín        130.0   
1  Apartamento  Arriendo  SurOriente          Oviedo  Medellín        150.0   
2  Apartamento  Arriendo  SurOriente       Castropol  Medellín        140.0   
3  Apartamento  Arriendo  SurOriente      El Poblado  Medellín        111.0   
4  Apartamento  Arriendo  SurOriente      El Poblado  Medellín        150.0   
5  Apartamento  Arriendo   Occidente   Florida Nueva  Medellín        130.0   
6  Apartamento  Arriendo   Occidente  Conquistadores  Medellín        120.0   
7  Apartamento  Arriendo  SurOriente      Aguacatala  Medellín        105.0   
8  Apartamento  Arriendo         NaN       los parra  Medellín        137.0   
9  Apartamento  Arriendo         NaN         POBLADO  Medellín        107.0   

   baños     precio  habitaciones    estrato  
0    2.0  1500000.0           3.0  Estrato 3  
1    3.0  3400000.0           3.0  Estrato 6  
2    3.0  5500000.0           2.0  Estrato 6  
3    3.0  2990000.0           3.0  Estrato 6  
4    3.0  3300000.0           3.0  Estrato 6  
5    3.0  2500000.0           3.0  Estrato 4  
6    3.0  3300000.0           3.0  Estrato 5  
7    3.0  4700000.0           3.0  Estrato 6  
8    3.0  3400000.0           3.0  Estrato 6  
9    2.0  5000000.0           5.0  Estrato 6

In [35]:
data.describe() #observo como estan distribuidos los datos

area_metros         baños        precio  habitaciones
count   22655.000000  22655.000000  2.265500e+04  22655.000000
mean      160.791145      2.606489  6.357925e+08      2.895122
std      2947.637190      1.117508  1.907184e+10      0.894714
min         1.000000      0.000000  3.000000e+05      0.000000
25%        71.000000      2.000000  1.350000e+08      2.000000
50%       100.000000      2.000000  3.800000e+08      3.000000
75%       148.000000      3.000000  6.200000e+08      3.000000
max    347347.000000     10.000000  2.750000e+12     20.000000

In [36]:
data.info() #observo los tipo de datos que contiene y si contiene nulos

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 22655 entries, 0 to 22654
Data columns (total 10 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   inmueble      22655 non-null  object 
 1   oferta        22655 non-null  object 
 2   region        16170 non-null  object 
 3   barrio        22652 non-null  object 
 4   ciudad        22655 non-null  object 
 5   area_metros   22655 non-null  float64
 6   baños         22655 non-null  float64
 7   precio        22655 non-null  float64
 8   habitaciones  22655 non-null  float64
 9   estrato       22655 non-null  object 
dtypes: float64(4), object(6)
memory usage: 1.7+ MB


In [37]:
data.isna().sum() #observo los datos vacios que trae cada columna

inmueble           0
oferta             0
region          6485
barrio             3
ciudad             0
area_metros        0
baños              0
precio             0
habitaciones       0
estrato            0
dtype: int64

Se puede observar que en la columna de región y barrio, existen valores faltantes, en region el total es de 6485 y en barrio el total es de 3

In [38]:
data.columns #veo el nombre de las columnas

Index(['inmueble', 'oferta', 'region', 'barrio', 'ciudad', 'area_metros',
       'baños', 'precio', 'habitaciones', 'estrato'],
      dtype='object')

**Tratamiento de los vacios**

In [39]:
data['region'].unique() #observo el contenido de los datos unicos 

array(['NorOriente', 'SurOriente', 'Occidente', nan, 'SurOccidente',
       'NorOccidente', 'Centro'], dtype=object)

In [40]:
import random

In [41]:
good_ones = ['NorOriente', 'SurOriente', 'Occidente','SurOccidente','NorOccidente', 'Centro'] #armo una lista con los datos correctos de la columna barrios 
region1 = [x for x in data['region']] #creo una funcion que recorra fila a fila los datos contenidos en la columna a tratar y los aloje en una lista
for r in range(0, len(region1)): #armo un for que itere por cada valor contenido en la lista que cree en el paso anterior, que comience en el valor 0 y se extienda por el tamaño total contenido en la lista
        if region1[r] == 'nan': 
            region1[r] = 'Unknown'
        elif region1[r] not in good_ones: #si el valor que contiene es distinto a alguno de los alojados en la lista good_ones
            region1[r] = random.choice(good_ones) #reemplazar de manera aleatoria por algun valor contenido en la lista good_ones, realizamos esto de este modo para que no se produzca un desbalance y los guarde en la lista creada

In [42]:
data['region'] = region1 #ahora le decimos que reemplace los datos contenidos en la columna a tratar por los contenidos en la lista creada

In [43]:
data.isna().sum() #volvemos a verificar los vacios y vemos que se han compleados los datos faltantes 

inmueble        0
oferta          0
region          0
barrio          3
ciudad          0
area_metros     0
baños           0
precio          0
habitaciones    0
estrato         0
dtype: int64

Antes de realizar este procedimiento en la columna barrio, que es la otra que contiene faltantes, vamos a normalizarla

In [44]:
pd.set_option("display.max_rows", None)#pido que me muestre el total de datos contenido y no un resumen 

In [45]:
data.barrio.value_counts()

El Poblado                                                                             2495
Laureles                                                                               1845
Calasanz                                                                                837
Robledo                                                                                 794
Castropol                                                                               758
Los Balsos                                                                              563
POBLADO                                                                                 499
Loma de los Bernal                                                                      492
Conquistadores                                                                          439
El Tesoro                                                                               390
Los Colores                                                                     

In [46]:
data['barrio']=data['barrio'].str.title() #funcion que transforma los datos en valores donde la primer letra es Mayúscula y el resto lo deja en minúscula

In [47]:
data= data.fillna('') #sustituyo los valores nulos por varios

In [48]:
data['barrio'].str.normalize('NFKD').str.encode('ascii', errors='ignore').str.decode('utf-8') #le quito las tildes

0                                             La Milagrosa
1                                                   Oviedo
2                                                Castropol
3                                               El Poblado
4                                               El Poblado
5                                            Florida Nueva
6                                           Conquistadores
7                                               Aguacatala
8                                                Los Parra
9                                                  Poblado
10                                            Patio Bonito
11                                  Santa M De Los Angeles
12                                              El Poblado
13                                  Santa M De Los Angeles
14                                               Castropol
15                                               Castropol
16                                                  Mani

In [49]:
data[data['barrio'].str.contains('Pobla')] #busco todas las palabras que contengan el substring Pobla

inmueble    oferta        region  \
3      Apartamento  Arriendo    SurOriente   
4      Apartamento  Arriendo    SurOriente   
9      Apartamento  Arriendo  NorOccidente   
12     Apartamento  Arriendo    NorOriente   
60     Apartamento  Arriendo  SurOccidente   
63     Apartamento  Arriendo    NorOriente   
71     Apartamento  Arriendo    SurOriente   
76     Apartamento  Arriendo    SurOriente   
79     Apartamento  Arriendo  NorOccidente   
110    Apartamento  Arriendo    SurOriente   
113    Apartamento  Arriendo    SurOriente   
131    Apartamento  Arriendo    SurOriente   
140    Apartamento  Arriendo    SurOriente   
151    Apartamento  Arriendo        Centro   
163    Apartamento  Arriendo  SurOccidente   
167    Apartamento  Arriendo    SurOriente   
183    Apartamento  Arriendo    SurOriente   
192    Apartamento  Arriendo    SurOriente   
198    Apartamento  Arriendo    SurOriente   
199    Apartamento  Arriendo    SurOriente   
205    Apartamento  Arriendo     Occidente   
206    Apartamento  Arriendo     Occidente   
209    Apartamento  Arriendo    SurOriente   
212    Apartamento  Arriendo    SurOriente   
213    Apartamento  Arriendo     Occidente   
221    Apartamento  Arriendo  SurOccidente   
225    Apartamento  Arriendo  NorOccidente   
226    Apartamento  Arriendo        Centro   
230    Apartamento  Arriendo    SurOriente   
233    Apartamento  Arriendo     Occidente   
240    Apartamento  Arriendo    NorOriente   
246    Apartamento  Arriendo    NorOriente   
254    Apartamento  Arriendo        Centro   
256    Apartamento  Arriendo  SurOccidente   
260    Apartamento  Arriendo    SurOriente   
261    Apartamento  Arriendo  SurOccidente   
264    Apartamento  Arriendo    SurOriente   
269    Apartamento  Arriendo     Occidente   
281    Apartamento  Arriendo  NorOccidente   
287    Apartamento  Arriendo    NorOriente   
288    Apartamento  Arriendo    SurOriente   
289    Apartamento  Arriendo    SurOriente   
301    Apartamento  Arriendo  SurOccidente   
303    Apartamento  Arriendo    SurOriente   
305    Apartamento  Arriendo     Occidente   
306    Apartamento  Arriendo    SurOriente   
310    Apartamento  Arriendo    SurOriente   
313    Apartamento  Arriendo    SurOriente   
317    Apartamento  Arriendo    NorOriente   
344    Apartamento  Arriendo  NorOccidente   
345    Apartamento  Arriendo    NorOriente   
358    Apartamento  Arriendo    SurOriente   
362    Apartamento  Arriendo    NorOriente   
364    Apartamento  Arriendo  SurOccidente   
367    Apartamento  Arriendo    SurOriente   
373    Apartamento  Arriendo    SurOriente   
374    Apartamento  Arriendo    SurOriente   
385    Apartamento  Arriendo    SurOriente   
387    Apartamento  Arriendo    SurOriente   
392    Apartamento  Arriendo    SurOriente   
408    Apartamento  Arriendo    NorOriente   
425    Apartamento  Arriendo     Occidente   
426    Apartamento  Arriendo  SurOccidente   
435    Apartamento  Arriendo    SurOriente   
437    Apartamento  Arriendo    SurOriente   
438    Apartamento  Arriendo    SurOriente   
439    Apartamento  Arriendo     Occidente   
462    Apartamento  Arriendo        Centro   
466    Apartamento  Arriendo     Occidente   
481    Apartamento  Arriendo    SurOriente   
485    Apartamento  Arriendo    NorOriente   
487    Apartamento  Arriendo  SurOccidente   
490    Apartamento  Arriendo  NorOccidente   
495    Apartamento  Arriendo    SurOriente   
496    Apartamento  Arriendo    NorOriente   
501    Apartamento  Arriendo    SurOriente   
506    Apartamento  Arriendo    SurOriente   
515    Apartamento  Arriendo    SurOriente   
530    Apartamento  Arriendo     Occidente   
538    Apartamento  Arriendo    SurOriente   
547    Apartamento  Arriendo    SurOriente   
548    Apartamento  Arriendo    SurOriente   
551    Apartamento  Arriendo    SurOriente   
552    Apartamento  Arriendo    SurOriente   
553    Apartamento  Arriendo    SurOriente   
556    Apartamento  Arriendo    SurOriente   
557    A

In [30]:
data.loc[data['barrio'].isin()] = 'Poblado'

In [ ]:

data.barrio = data.barrio.str.replace('El Castillo El Poblado'
El Poblado Frontera	
El Poblado La Linde	
El Poblado Los Parra	
El Poblado Ciudad Del Rió	
Alejandria El Poblado Medellín	
El Poblado Clinica Medellin	
Sur El Poblado	
El Tesoro Parte Alta El Poblado	
Loma De San Julián El Poblado	
El Poblado Transversal Superior	
El Poblado Tomatera	
El Poblado Loma Del Tesoro	
Pobladp Provenza	
Las Palmas El Poblado	
Los Gonzalez El Poblado	
El Poblado Lv	
El Poblado Sur	
El Poblado Loma De Los Parra	
El Campestre El Poblado	
Alejandria El Poblado	
El Poblado Parte Baja	
El Poblado Oviedo	
Astorga Parque Del El Poblado	
El Poblado Loma De San Julian	
El Poblado Sector Manila	
El Poblado Loma El Indio	
El Poblado Loma Del Indio	
El Poblado Loma De Los Gonzalez	

In [24]:
data.barrio = data.barrio.str.replace('Las Palmas Country Club El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('El Tesoro El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Patio Bonito','El Poblado')
data.barrio = data.barrio.str.replace('El El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('Oviedo El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('Santamaria De Los Ángeles El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('Altos De El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('Sur Oriente El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Sector Bagatela','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado N 1','El Poblado')
data.barrio = data.barrio.str.replace('Alejandría El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Loma Marianito','El Poblado')
data.barrio = data.barrio.str.replace('Los Balsos El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Vía Las Palmas','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado San Julian','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Los Yarumos','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Sector La Aguacatala','El Poblado')
data.barrio = data.barrio.str.replace('Ciudad Del Rio El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('Loma Del Indio El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('Avenida Del El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Campestre','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Loma De Encierro','El Poblado')
data.barrio = data.barrio.str.replace('Las Palmas Intercontinental Country Club El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('Transversal Superior El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Alto','El Poblado')
data.barrio = data.barrio.str.replace('San Diego El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('Loma Del Indio El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Vía Las Palmas','El Poblado')
data.barrio = data.barrio.str.replace('Loma Del Indio El Poblado','El Poblado')

In [23]:
data.barrio = data.barrio.str.replace('El El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('El El El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('El El Poblado Patio Bonito','El Poblado')
data.barrio = data.barrio.str.replace('El Tesoro El El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('Las Palmas Country Club El El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Altos Del El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('La Frontera El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('Altos Del El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('Santamaria De Los Ángeles El El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('Oviedo El El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Medellin','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Balsos Con La Inferir','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Loma Los Gonzalez','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Medellin','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Balsos Con La Inferir','El Poblado')
data.barrio = data.barrio.str.replace('Altos Del El Poblado','El Poblado')
#data.barrio = data.barrio.str.replace('Poblado','El Poblado')
data.barrio = data.barrio.str.replace('Poblado Entre Los Balsos Y Los Gonzalez','El Poblado')
data.barrio = data.barrio.str.replace('Las Palmas Country Club El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado San Lucas','El Poblado')
data.barrio = data.barrio.str.replace('Altos Del Poblado','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado La Calera','El Poblado')
data.barrio = data.barrio.str.replace('Poblado Oa','El Poblado')
data.barrio = data.barrio.str.replace('Poblado El Campestre	','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado El Tesoro','El Poblado')
data.barrio = data.barrio.str.replace('La Linde Poblado','El Poblado')
data.barrio = data.barrio.str.replace('El Tesoro El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado San Fernando','El Poblado')
data.barrio = data.barrio.str.replace('Poblado Alejandria','El Poblado')
data.barrio = data.barrio.str.replace('Poblado Santa María De Los Ángeles','El Poblado')
data.barrio = data.barrio.str.replace('Poblado Loma Del Encierro','El Poblado')
data.barrio = data.barrio.str.replace('Poblado Los Balsos','El Poblado')
data.barrio = data.barrio.str.replace('Poblado La Tomatera','El Poblado')
data.barrio = data.barrio.str.replace('Poblado La Concha','El Poblado')
data.barrio = data.barrio.str.replace('Poblado Castropol','El Poblado')
data.barrio = data.barrio.str.replace('Poblado Sta Maria De Los Angeles','El Poblado')
data.barrio = data.barrio.str.replace('Santa Maria De Los Angeles Poblado','El Poblado')
data.barrio = data.barrio.str.replace('Poblado Las Santas','El Poblado')
data.barrio = data.barrio.str.replace('Sur Poblado','El Poblado')
data.barrio = data.barrio.str.replace('Sur Poblado La Frontera','El Poblado')
data.barrio = data.barrio.str.replace('Poblado Interlomas','El Poblado')
data.barrio = data.barrio.str.replace('Poblado Las Lomas 1','El Poblado')
data.barrio = data.barrio.str.replace('Poblado Las Lomas','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Las Palmas','El Poblado')
data.barrio = data.barrio.str.replace('Poblado Altos Del Poblado','El Poblado')
data.barrio = data.barrio.str.replace('El Tesoro Poblado','El Poblado')
data.barrio = data.barrio.str.replace('Poblado Loma Los Balsos','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Lalinde','El Poblado')
data.barrio = data.barrio.str.replace('Poblado Cola Del Zorro','El Poblado')
data.barrio = data.barrio.str.replace('Poblado Balsos 2','El Poblado')
data.barrio = data.barrio.str.replace('Poblado Campestre Drive Inn','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Astorga','El Poblado')
data.barrio = data.barrio.str.replace('Poblado Balsos 2','El Poblado')
data.barrio = data.barrio.str.replace('Poblado Campestre Drive Inn','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Astorga','El Poblado')
data.barrio = data.barrio.str.replace('Las Palmas Country Club El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('La Linde El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Alejandría','El Poblado')
data.barrio = data.barrio.str.replace('Santa Maria De Los Angeles El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('Sur El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('Sur El Poblado La Frontera','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado El Campestre','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado La Frontera','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Santa Maria De Los Angeles','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Loma Lalinde','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Loma Del Campestre','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado El Campestre','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Loma De Los Balsos','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Provenza','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Sector Oviedo','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Altos Delpoblado','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Suroriente','El Poblado')
data.barrio = data.barrio.str.replace('San Lucas El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('EEl Poblado El Guamal','El Poblado')
data.barrio = data.barrio.str.replace('San Lucas El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Vizcaya','El Poblado')
data.barrio = data.barrio.str.replace('Vegas Del El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado La Florida','El Poblado')
data.barrio = data.barrio.str.replace('Castropol El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('El Alejandria El Poblado','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Milla De Oro','El Poblado')
data.barrio = data.barrio.str.replace('ElEl Poblado Campestre','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado 2','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Ciudad Del Rio','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Manila','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado Las Loma 2','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado La Aguacatala','El Poblado')
data.barrio = data.barrio.str.replace('El Poblado La Aguacatala','El Poblado')